#### Rewrite SQL stored procedure to pyspark

PRC_SYNC_DATA & PRC_SEL_XML_PARSER_RESULT

In [0]:
PROJECT_NAME = 'BIFC_OSCE'
DB = 'TEST' 
START_DATE = '2022-01-18' 
END_DATE = '2022-01-20'

In [0]:
import pyspark.sql.functions as F
from pyspark.sql.types import StructField, StructType, StringType, ArrayType, LongType, TimestampType, BinaryType, IntegerType, DateType
from datetime import datetime, timedelta
# from pyspark.sql import Window
from pyspark.sql.window import Window
from pyspark.sql.functions import row_number

from functools import reduce
from pyspark.sql import DataFrame

from pyspark.sql.window import Window
from pyspark.sql.functions import monotonically_increasing_id, row_number

windowSpec  = Window.partitionBy("m.column_name").orderBy(F.col("data_type").desc())


In [0]:
start_date= (datetime.now() + timedelta(days = -30)).strftime("%Y-%m-%d")
end_date = datetime.now().strftime("%Y-%m-%d")
print("start_date:",start_date)
print("end_date:",end_date)

In [0]:
#synapse 
spark.conf.set('fs.azure.account.key.gdwpocdls.dfs.core.windows.net', dbutils.secrets.get(scope = 'BIFC-asagdwpocws-etl', key = 'StorageAccount-gdwpocdls-AccessKey'));
_url = dbutils.secrets.get(scope = 'BIFC-asagdwpocws-etl', key = 'Synapse-asagdwpocetl-ConnectionString');

**Load Synaspe Table**

In [0]:
df_raw = (spark.read
          .format('com.databricks.spark.sqldw')
          .option('url', _url)
          .option('tempDir', 'abfss://bifconnect@gdwpocdls.dfs.core.windows.net/tempDirs')
          .option('useAzureMSI', 'true')
          .option('dbTable', 'BIFC.TBL_DATA_RAW')
          .load()
          .filter(F.col('file_date') > START_DATE)
          .filter(F.col('file_date') < END_DATE)
          .filter(F.col('source') == "OSCE")
          .filter(F.col('xml_version') == "2.0" )
          .withColumn('file_date', F.date_format(F.col('file_date'),"yyyy/MM/dd"))
          )
display(df_raw)

file_id source xml_version file_name file_content file_date ip 1086591924 OSCE 2.0 fd7aaa7071_202201191853517100_2.0_210.130.216.3 1 2.0 2022-01-19 18:53:50 2592974b-4310-4458-902c-fcaf43e93d75 14.0.9233 0 4 1 2 1 13.0.5026.0;SP2;Express Edition (64-bit) 0 0 0 0 0 0 0 0 0 ja 1 0 10.0.14393 1041 9233 0 0 0 0 1 0 0 1 0 1 http 1 0 0 1 1 0 0 0 0 0 0 0 0 0 0 0 0 995 0 11 0 0 0 0 2022/01/19 210.130.216.3 1086591890 OSCE 2.0 fb0cc3c0d8_202201191900175574_2.0_202.248.120.232 1 2.0 2022-01-19 19:00:13 1da7087d-5cd0-4503-80c6-0ba447f2be1b 14.0.8378 0 1 2 2 13.0.5026.0;SP2;Express Edition (64-bit) 0 0 0 0 0 0 0 0 0 ja 1 0 10.0.17763 1041 8378 0 1 0 0 1 0 0 1 0 1 http 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 4 0 2 0 1 1 0 2022/01/19 202.248.120.232 1086591856 OSCE 2.0 f833fafbd9_202201191900554614_2.0_210.227.119.120 1 2.0 2022-01-19 19:00:55 7e6dc3c6-1a3c-4ae0-8ce6-78bbdff3565c 14.0.9645 0 5 1 2 2 13.0.5026.0;SP2;Express Edition (64-bit) 0 0 0 0 2 0 0 0 0 ja 1 1 10.0.14393 1041 9645 0 0 0 0 1 0 0 1 1 0 1 http 1 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 null
 51 0 5 0 1 1 1 1 1 1 -1 1 1 2022/01/19 210.227.119.120 1086591822 OSCE 2.0 f548c872d7_202201191900301305_2.0_202.32.17.175 1 2.0 2022-01-19 19:00:29 db7b5a8f-5787-4775-89c6-23b4e91e0fe5 14.0.9675 0 5 1 2 2 13.0.5026.0;SP2;Express Edition (64-bit) 0 0 0 0 0 0 0 0 0 ja 1 0 6.3.9600 1041 9675 0 0 0 0 1 0 0 1 1 0 1 http 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 null
 206 0 36 0 1 1 0 1 1 1 -1 1 1 2022/01/19 202.32.17.175 1086591788 OSCE 2.0 f2530f8631_202201191907339179_2.0_195.235.203.130 1 2.0 2022-01-19 19:07:30 ae6e182b-e3dc-4950-8462-e4a364f39043 14.0.10048 0 6 1 2 1 13.0.5103.6;SP2;Express Edition (64-bit) 0 0 0 0 0 0 0 0 0 en 1 0 10.0.17763 3082 10048 0 0 0 0 1 0 0 1 1 50 604800 240 1440 0 7 0 7 0 1 http 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 null
 1 1 -1 -1 -1 -1 0 -1 0 0 1 2 7 2 3 0 1 0 0 80 0 0 0 0 0 0 0 0 0 0 0 0 0 408 0 26 0 1 1 0 1 1 1 -1 1 -1 1 2022/01/19 195.235.203.130 1086591752 OSCE 2.0 ef749eb721_202201191900465962_2.0_193.49.209.114 1 2.0 2022-01-19 19:00:45 4a79055a-f11a-448f-baee-071193d0b725 14.0.9675 0 5 1 2 2 15.0.2000.5;RTM;Express Edition (64-bit) 0 0 0 0 0 0 0 0 0 fr 1 0 10.0.14393 1036 9675 0 1 0 0 1 0 0 1 1 0 1 http 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 null
 128 0 2 0 1 1 1 1 1 1 -1 1 1 2022/01/19 193.49.209.114 1086591720 OSCE 2.0 ec651491f7_202201191900591003_2.0_217.12.24.167 1 2.0 2022-01-19 19:00:57 a6bf598e-3aa8-44c7-8213-a73decf37442 14.0.9167 0 4 1 2 1 13.0.5026.0;SP2;Express Edition (64-bit) 0 0 2 0 2 0 0 0 0 es 1 1 10.0.14393 3082 9167 0 1 0 0 1 0 0 1 0 1 http 1 0 0 1 1 0 0 0 0 0 0 0 0 0 0 0 0 201 0 1 0 1 1 1 2022/01/19 217.12.24.167 1086591686 OSCE 2.0 e980d0c277_202201191900329129_2.0_165.225.200.147 1 2.0 2022-01-19 19:00:30 6dee24fd-afde-4def-b52d-d2139e2abf10 14.0.9675 0 5 1 2 1 13.0.5026.0;SP2;Express Edition (64-bit) 0 0 0 0 0 0 0 0 0 en 1 1 10.0.14393 1033 9675 0 1 0 0 1 0 0 1 1 0 0 http 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 null
 6 0 2 3.0.0.3061 en-US 0 0 0 0 0 0 0 0 0 1 1 1 -1 1 1 2022/01/19 165.225.200.147 1086591652 OSCE 2.0 e7a00438ec_202201191829093815_2.0_103.51.66.90 1 2.0 2022-01-20 00:00:14 22b7cfa0-d056-4533-90c5-8f054f48c7c4 12.0.6040 1 1 0 0 0 0 0 0 0 0 0 en 1 1 6.1.7601 1054 6040 0 1 0 0 1 0 0 1 http 1 0 0 0 1 1 0 1 1 1 1 0 0 0 0 0 0 0 0 104 5 17 0 1 1 1 2022/01/19 103.51.66.90 1086591613 OSCE 2.0 e5196857e2_202201191905353352_2.0_210.165.72.185 1 2.0 2022-01-19 19:01:00 094fe113-a13e-414b-b460-697d898a284d 14.0.9233 0 4 1 2 2 12.0.5223.6;SP2;Standard Edition (64-bit) 0 0 0 0 0 0 0 0 0 ja 1 1 6.3.9600 1041 9233 0 0 0 0 1 0 0 1 0 1 http 1 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 7 0 1 0 1 1 0 2022/01/19 210.165.72.185 1086591580 OSCE 2.0 e21853f404_202201191900287985_2.0_113.35.156.211 1 2.0 2022-01-19 19:00:26 ef20e075-2c63-4364-ab72-9c8cd3253b85 14.0.9167 0 4 1 2 1 13.0.5026.0;SP2;Express Edition (64-bit) 0 0 0 0 0 0 0 0 0 ja 1 0 10.0.17763 1041 9167 0 1 0 0 1 0 0 1 0 1 http 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 366 0 6 0 0 0 0 2022/01/1

In [0]:
df_group = (spark.read
            .format('com.databricks.spark.sqldw')
            .option('url', _url)
            .option('tempDir', 'abfss://bifconnect@gdwpocdls.dfs.core.windows.net/tempDirs')
            .option('useAzureMSI', 'true')
            .option('dbTable', 'BIFC_ETL.TBL_PROJECT_GROUP')
            .load()
            .filter(F.col('Project_Name') == PROJECT_NAME)
            )

df_parse_config = (spark.read
            .format('com.databricks.spark.sqldw')
                    .option('url', _url)
                    .option('tempDir', 'abfss://bifconnect@gdwpocdls.dfs.core.windows.net/tempDirs')
                    .option('useAzureMSI', 'true')
                    .option('dbTable', 'BIFC_ETL.TBL_XML_PARSER_CONFIG')
                    .load()
                    .withColumn("sort",F.col("sort").cast(IntegerType()))
                   )

df_raw_config = (spark.read
                    .format('com.databricks.spark.sqldw')
                    .option('url', _url)
                    .option('tempDir', 'abfss://bifconnect@gdwpocdls.dfs.core.windows.net/tempDirs')
                    .option('useAzureMSI', 'true')
                    .option('dbTable', 'BIFC_ETL.TBL_XML_RAW_CONFIG')
                    .load()
                   )


In [0]:
df_raw.write.format('delta').mode('overwrite').save('/mnt/bifconnect/TBL_DATA_RAW1')

In [0]:
df_group.write.format('delta').mode('overwrite').save('/mnt/bifconnect/TBL_PROJECT_GROUP')
df_parse_config.write.format('delta').mode('overwrite').save('/mnt/bifconnect/TBL_XML_PARSER_CONFIG')
df_raw_config.write.format('delta').mode('overwrite').save('/mnt/bifconnect/TBL_XML_RAW_CONFIG')

In [0]:
%sql
select * from TBL_DATA_RAW
-- CREATE TABLE default.TBL_DATA_RAW USING DELTA LOCATION '/mnt/bifconnect/TBL_DATA_RAW1'
-- CREATE TABLE default.TBL_PROJECT_GROUP USING DELTA LOCATION '/mnt/bifconnect/TBL_PROJECT_GROUP'
-- CREATE TABLE default.TBL_XML_PARSER_CONFIGb USING DELTA LOCATION '/mnt/bifconnect/TBL_XML_PARSER_CONFIG'
-- CREATE TABLE default.TBL_XML_RAW_CONFIG USING DELTA LOCATION '/mnt/bifconnect/TBL_XML_RAW_CONFIG'

file_id source xml_version file_name file_content file_date ip 1086616491 OSCE 2.0 ff7e896628_202201192300536682_2.0_192.71.204.13 1 2.0 2022-01-20 00:00:48 8a7f6100-67a6-4fc0-ad05-5eeba59db73c 12.0.6046 1 2 1 0 0 0 0 1 72 1 50 en 1 1 10.0.14393 1053 6046 0 0 0 0 1 0 2 1 http 1 1 1 1 1 1 1 1 1 1 1 0 0 0 0 0 0 1 0 710 0 330 0 1 1 0 2022/01/19 192.71.204.13 1086616459 OSCE 2.0 fe8990f13e_202201192200324633_2.0_223.29.63.170 1 2.0 2022-01-19 22:00:31 6356f321-2507-4583-8121-09ffccb61e79 14.0.9167 0 4 1 2 2 12.0.5000.0;SP2;Express Edition 0 0 0 0 0 0 0 0 0 ja 1 0 10.0.14393 1041 9167 0 1 0 0 1 0 0 1 0 1 http 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 63 0 4 0 1 1 1 2022/01/19 223.29.63.170 1086616427 OSCE 2.0 fdb3552e87_202201192201129895_2.0_143.111.84.227 1 2.0 2022-01-19 22:00:58 6dd95f48-73a7-4470-8e31-ebc6655ebb17 14.0.10048 0 6 1 2 1 13.0.5698.0;SP2;Enterprise Edition: Core-based Licensing (64-bit) 0 0 0 0 0 0 0 0 0 en 1 0 10.0.14393 1033 10048 1 1 1 0 1 1 0 1 1 50 604800 240 1440 0 0 0 7 0 1 http 1 1 1 1 1 0 0 0 0 0 0 0 0 0 1 0 1 0 0 0 1 {"CustomPolicyTrackingInfo":[{"Policy":"{\"AddAllPolicy\":null}","PolicyID":"1dfc644e-00a7-4e9d-88a7-ca4a0b6b4f7e","PolicyName":"ac_default_policy-schscn","UsedCount":"237"},{"Policy":"{\"AddAllPolicy\":null}","PolicyID":"83a38c03-588a-4b8c-80f4-6d8a5b88322c","PolicyName":"_!_mdanderson_2am","UsedCount":"1"},{"Policy":"{\"AddAllPolicy\":null}","PolicyID":"cfd835f2-7131-49f1-a2c0-aaaba0a503e0","PolicyName":"_!_radstation","UsedCount":"1"},{"Policy":"{\"AddAllPolicy\":null}","PolicyID":"F900-0000-FFFF-0000-000000000000","PolicyName":"","UsedCount":"1"}]}
 1 1 -1 -1 -1 -1 0 -1 0 0 1 2 7 2 3 0 1 0 0 80 0 0 0 0 0 0 0 0 0 0 0 0 0 0 239 0 88 0 1 1 1 1 1 1 -1 1 -1 1 2022/01/19 143.111.84.227 1086616363 OSCE 2.0 fb7bffb412_202201192302154014_2.0_91.220.125.48 1 2.0 2022-01-20 00:02:06 dc5eced1-22da-414e-9711-a2d047c1ff01 12.0.6046 1 1 0 0 0 0 0 0 0 0 0 de 1 1 10.0.14393 1031 6046 1 0 0 1 1 0 0 1 http 1 0 0 1 1 1 1 1 1 1 1 0 0 0 0 0 0 0 0 19 6 23 0 1 1 0 2022/01/19 91.220.125.48 1086616329 OSCE 2.0 faa9d4c470_202201192225344553_2.0_153.216.223.63 1 2.0 2022-01-20 07:25:31 4b0f4f79-d19a-4779-bb3a-441e1e94ef80 12.0.6063 1 1 0 0 0 0 0 0 0 0 0 ja 1 1 6.3.9600 1041 6063 0 0 0 0 1 0 0 0 http 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 25 5 6 0 1 1 1 2022/01/19 153.216.223.63 1086616295 OSCE 2.0 f9bc5a8e70_202201192300380827_2.0_213.253.213.70 1 2.0 2022-01-19 23:00:28 4a695cba-8638-420d-9bc9-8743a056afcf 14.0.2012 0 1 2 2 14.0.1000.169;RTM;Express Edition (64-bit) 0 0 0 0 0 0 0 0 0 en 1 0 10.0.17763 1038 2012 0 1 0 0 1 0 0 1 0 1 http 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 5 0 4 3.0.0.1160 en-US 0 0 0 0 0 2022/01/19 213.253.213.70 1086616261 OSCE 2.0 f8fc286c8a_202201192300498774_2.0_77.159.185.142 1 2.0 2022-01-20 00:00:44 18c4dd15-fa1e-4138-b4ae-9a3c41836325 12.0.5261 1 1 0 0 0 0 1 0 0 0 0 fr 1 1 6.3.9600 1036 5261 0 0 0 0 1 0 0 1 http 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 85 5 16 2022/01/19 77.159.185.142 1086616227 OSCE 2.0 f7c12b277f_202201192300563713_2.0_219.59.56.22 1 2.0 2022-01-19 23:00:45 ab5186c7-8aa5-4b0d-a605-8d0fe9c4058b 14.0.9120 0 4 1 2 2 12.0.6024.0;SP3;Express Edition 0 0 0 0 0 0 0 0 0 ja 1 0 10.0.17763 1041 9120 0 1 0 0 1 0 0 1 0 0 http 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 131 0 6 0 0 0 0 2022/01/19 219.59.56.22 1086616162 OSCE 2.0 f5c9263cfd_202201192200306758_2.0_113.161.208.185 1 2.0 2022-01-19 22:00:26 4d8aa51c-eb54-4b90-872b-a37b63eed9e6 14.0.9675 0 5 1 2 1 13.0.5026.0;SP2;Express Edition (64-bit) 0 0 0 0 0 0 0 0 0 en 1 0 6.3.9600 1033 9675 0 1 0 0 1 0 0 1 1 0 1 http 1 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 null
 22 0 8 3.0.0.3061 en-US 0 0 0 0 0 0 1 1 1 1 1 1 -1 1 1 2022/01/19 113.161.208.185 1086616129 OSCE 2.0 f4b85f2236_202201192114100004_2.0_153.92.81.194 1 2.0 2022-01-19 21:14:00 249a8707-7355-4d2b-9d4b-da804a945181 14.0.9629 0 5 1 2 1 13.0.5103.6;SP2;Express Edition (64-bit) 0 0 0 0 0 0 0 0 0 en 1 1 10.0.14393 1031 9629 0 1 0 0 1 0 0 1 1 0 1 http 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0

**Generate Result Type 1 & Result Type 2 table create script**

In [0]:
#ResultType 1:Name/Value Pair
df1 = (df_group
    .filter('Name_Value_Pair_Table_Name is not null')
    .withColumn('ResultType', F.lit('1'))
    .withColumn('Table_Name', F.col('Name_Value_Pair_Table_Name'))
    .withColumn('With_File_Date', F.when(F.col('With_File_Date').isNull(), F.lit(False)).otherwise(F.col('With_File_Date'))) 
    .select('Group_Name','Table_Schema','Table_Name','ResultType','Name_Value_Pair_Table_Name','Data_Source_View','With_File_Date','project_group_id')
     )

display(df1.limit(5))

In [0]:
df1_rdd = df1.collect()

#ResultType 1:Name/Value Pair

type1_create_table_list = []

for row in df1_rdd:

    data={}
    Group_Name = row.Group_Name
    Table_Name = row.Table_Name
    Table_Schema = row.Table_Schema
    Data_Source_View = row.Data_Source_View
    create = ''
    sql = '[File_ID] [bigint]'
    col = '[File_ID]'
    fullTableName = f'{DB}.{row.Table_Name}'
    project_group_id = row.project_group_id
    if row.With_File_Date:
        sql = sql + ',[File_Date] [date]'
        col = col + ',[File_Date]'
    
    print(fullTableName)

    if ( Data_Source_View == None ):

        df_config_table = (df_parse_config.alias('m')
                          .filter(f'project_group_id=={project_group_id}')
                          )

        df_config_table_rdd = df_config_table.select('category','data_type','data_length').collect()

        category = df_config_table_rdd[1][0]
        data_type = df_config_table_rdd[1][1]
        data_length = df_config_table_rdd[1][2]

        if (len(category)) > 0:
            sql = sql + ', [group] [varchar](100) NOT NULL, [column_name] [varchar](1000) NULL, [column_value] [nvarchar](4000) NULL'
        else:
            colcount = '[count] [bigint] NULL' if data_type == 'int' else f'[Value] [nvarchar](20) NULL'
            sql = sql + ', [Category] [varchar](300) NOT NULL,[Name] [varchar](1000) NULL,' + colcount
 

    create = f'create table {fullTableName}({sql})WITH(DISTRIBUTION = ROUND_ROBIN,CLUSTERED COLUMNSTORE INDEX)'
    data['fullTableName'] = fullTableName
    data['project_group_id'] = project_group_id
    data['group_name'] = Group_Name
    data['result_type'] = 1
    data['col'] = ''
    data['create'] = create
    data['data_source_view'] = Data_Source_View
    data['with_file_date'] = row.With_File_Date    
    type1_create_table_list.append(data)


In [0]:
#ResultType 2:Flat table

df2 = (df_group
    .filter('Flat_Table_Name is not null')
    .withColumn('ResultType', F.lit('2'))
    .withColumn('Table_Name', F.col('Flat_Table_Name'))
    .withColumn('With_File_Date', F.when(F.col('With_File_Date').isNull(), F.lit(False)).otherwise(F.col('With_File_Date'))) 
    .select('Group_Name','Table_Schema','Table_Name','ResultType','Name_Value_Pair_Table_Name','Data_Source_View','With_File_Date','project_group_id')
     )
display(df2.limit(5))

In [0]:
windowSpec  = Window.partitionBy("m.column_name").orderBy(F.col("data_type").desc())

df2_rdd = df2.collect()

# ResultType 2:Flat table ceate table schema

type2_create_table_list = []

for row in df2_rdd:

    data={}
    Group_Name = row.Group_Name
    Table_Name = row.Table_Name
    Table_Schema = row.Table_Schema
    Data_Source_View = row.Data_Source_View
    create = ''
    sql = '[File_ID] [bigint]'
    col = '[File_ID]'
    fullTableName = f'{DB}.{row.Table_Name}'
    project_group_id = row.project_group_id
   
    if row.With_File_Date:
        sql = sql + ',[File_Date] [date]'
        col = col + ',[File_Date]'
    
    print(fullTableName)

    if ( Data_Source_View == None ):

        df_config_sort = df_parse_config.groupBy('project_group_id','column_name').agg(F.min('sort').alias('sort'))
        
        df_config_table = (df_parse_config.alias('m')
                          .filter(f'project_group_id=={project_group_id}')
                          .join(df_config_sort.alias('s'), [F.col('m.project_group_id')==F.col('s.project_group_id'),
                                                                        F.col('m.column_name')==F.col('s.column_name')], 'inner')
                          .select('m.column_name','data_type','data_length','s.sort')
                          .withColumn("data_length",F.col("data_length").cast(IntegerType()))
                          .withColumn("id",row_number().over(windowSpec))
                          .filter('id == 1')
                          .orderBy(F.col("sort").asc())
                          )

        df_config_table_rdd = df_config_table.collect()
        for t in df_config_table_rdd:
            #print(t)
            lenght = f'({t.data_length})' if t.data_length != None else ''
            sql = sql + f',[{t.column_name}] [{t.data_type}]{lenght}' 
            col = col + f',[{t.column_name}]'
        create = f'create table {fullTableName}({sql})WITH(DISTRIBUTION = ROUND_ROBIN,CLUSTERED COLUMNSTORE INDEX)'
        data['fullTableName'] = fullTableName
        data['project_group_id'] = project_group_id
        data['group_name'] = Group_Name
        data['result_type'] = 2
        data['col'] = col
        data['create'] = create
        data['data_source_view'] = Data_Source_View
        data['with_file_date'] = row.With_File_Date
        type2_create_table_list.append(data)
    
    

In [0]:
create_list = type1_create_table_list + type2_create_table_list
create_rdd= spark.sparkContext.parallelize(create_list)
create_df = (spark
             .createDataFrame(create_rdd)
            )
display(create_df.filter("result_type == 2"))

In [0]:
create_df.write.format('delta').mode('overwrite').save('/mnt/trendmicrobif/create_df')

In [0]:
create_df = spark.read.format('delta').load('/mnt/trendmicrobif/create_df')
display(create_df)
create_df.createOrReplaceTempView("create_df")

col create data_source_view fullTableName group_name project_group_id result_type with_file_date [File_ID],[File_Date],[Product_PccNT_Build],[GUID],[Product_Version_Build],[Protocol_Version],[Seat] create table TEST.OSCE_Feedback_Main([File_ID] [bigint],[File_Date] [date],[Product_PccNT_Build] [varchar](15),[GUID] [varchar](54),[Product_Version_Build] [varchar](14),[Protocol_Version] [int],[Seat] [int])WITH(DISTRIBUTION = ROUND_ROBIN,CLUSTERED COLUMNSTORE INDEX) null TEST.OSCE_Feedback_Main OSCE_1.0_Feedback_Main 240 2 true [File_ID],[File_Date],[Count],[DB_Size],[Platform_Type] create table TEST.OSCE_iES_Endpoint_Policy_DB_Size([File_ID] [bigint],[File_Date] [date],[Count] [int],[DB_Size] [int],[Platform_Type] [varchar](13))WITH(DISTRIBUTION = ROUND_ROBIN,CLUSTERED COLUMNSTORE INDEX) null TEST.OSCE_iES_Endpoint_Policy_DB_Size OSCE_2.0_iES_Endpoint_Policy_DB_Size 432 2 true [File_ID],[File_Date],[Count],[Source_Type] create table TEST.OSCE_iES_Server_Impact_Eval_Source([File_ID] [bigint],[File_Date] [date],[Count] [int],[Source_Type] [varchar](34))WITH(DISTRIBUTION = ROUND_ROBIN,CLUSTERED COLUMNSTORE INDEX) null TEST.OSCE_iES_Server_Impact_Eval_Source OSCE_2.0_iES_Server_Impact_Eval_Source 440 2 true [File_ID],[File_Date],[Count],[Match_Method_ID] create table TEST.OSCE_iAC_Agent_Rule_Method_Result([File_ID] [bigint],[File_Date] [date],[Count] [int],[Match_Method_ID] [int])WITH(DISTRIBUTION = ROUND_ROBIN,CLUSTERED COLUMNSTORE INDEX) null TEST.OSCE_iAC_Agent_Rule_Method_Result OSCE_2.0_iAC_Agent_Rule_Method_Result 426 2 true [File_ID],[File_Date],[Count],[Upload_Enabled],[Platform_Type] create table TEST.OSCE_iES_Endpoint_Policy_Meta_Upload([File_ID] [bigint],[File_Date] [date],[Count] [int],[Upload_Enabled] [int],[Platform_Type] [varchar](13))WITH(DISTRIBUTION = ROUND_ROBIN,CLUSTERED COLUMNSTORE INDEX) null TEST.OSCE_iES_Endpoint_Policy_Meta_Upload OSCE_2.0_iES_Endpoint_Policy_Meta_Upload 434 2 true [File_ID],[File_Date],[AC] create table TEST.OSCE_iVP_AC([File_ID] [bigint],[File_Date] [date],[AC] [varchar](65))WITH(DISTRIBUTION = ROUND_ROBIN,CLUSTERED COLUMNSTORE INDEX) null TEST.OSCE_iVP_AC OSCE_2.0_iVP_AC 442 2 true [File_ID],[File_Date],[Last_Updated_Time],[Feedback_Version],[Seat],[S_Agent_Grouping],[TMCM_Enabled],[Product_Database_Mode],[GUID],[Product_HTTP_Server_Type],[Product_OS_Language],[Product_OS_Type],[Product_OS_Code],[Product_PccNT_Build],[Product_Language],[Product_Version_Build],[Product_Upgrade],[Protocol_Version],[Product_SQL_Auth_Mode],[E_Meerkat_Log_Only_Disabled_Count],[E_Meerkat_Log_Only_Enabled_Count],[S_BT_SO_Use_CM],[S_Role_Service],[DAC_Policy_Count],[DLP_Policy_Count],[S_Agent_OUS_Count],[S_Allow_Agent_Update_From_OUS],[S_Custom_Scan_Server_List_Count],[S_Endpoint_Location],[S_Hybrid_Mode],[S_Internal_Proxy_Type],[S_Use_Custom_Scan_Server],[iAC_Agent_Enabled_Count],[iAC_Base_Action],[iAC_Policy],[iAC_Product_Language],[iAC_Product_Version],[iAC_Assign_Rule_Enabled],[iAC_Assign_Rule_With_AD_Enabled],[iAC_Config_Rule_Enabled],[iAC_OS_Arch],[iAC_OS_Branch],[iAC_OS_Build],[iAC_OS_Platform],[iAC_OS_Service_Pack],[iAC_OS_Version],[iAC_OS_Version_Number],[iATAS_Agent_Enabled_Count],[iES_Is_MDR_Enabled],[iES_Maximum_Metadata_Storage],[iES_Product_Build],[iES_Product_Version],[iVP_Agent_Enabled_Count],[TMCM_Proxy_Sock],[S_NAT_Enabled],[Product_Patch],[Product_Service_Pack_Patch],[Product_Service_Pack],[S_Sample_Submission_Count_In_BIF_Period],[Product_SQL_Server_Verion],[S_Update_Source_Type],[S_Use_CM_Proxy],[iAC_Config_Policy_Enabled],[iVP_Endpoint_IPS_Enabled_Client_Count],[iVP_Manual_Enable_IPS_Rule],[iES_Maximum_Redis_Storage],[iES_SaaS_Storage_License],[XDR_Onboard_Accept_XBC],[XDR_Onboard_Get_Onboard_URL],[XDR_Onboard_Is_Onboarded],[XDR_Onboard_Prepare_XBC_Patch],[BIF_Status],[CLP_ID],[BIF_Feedback_Days],[XDR_Onboard_Enable_Onboard_Promotion],[XDR_Onboard_Enable_Pre_Onboard],[XDR_Onboard_Enable_Scheduled_Preonboard],[XDR_Onboard_XBC_Download_Mac_Universal],[XDR_Onboard_XBC_Download_URL_Win32],[XDR_On

**Create table in synapse if doesn't exist**

Create table script is DDL, Spark driver is not a general-purpose database library, we cannot use spark.write or spark.read to run DDL or execute Stored Procedure. But the Spark driver is built on top of the JDBC driver, which you can use directly in either Scala or Java

In [0]:
%scala
import java.sql.DriverManager
import java.sql.Connection
import java.util.Properties

//  Create the JDBC URL without passing in the user and password parameters.
spark.conf.set("fs.azure.account.key.gdwpocdls.dfs.core.windows.net", dbutils.secrets.get(scope = "BIFC-asagdwpocws-etl", key = "StorageAccount-gdwpocdls-AccessKey"));
val _url = dbutils.secrets.get(scope = "BIFC-asagdwpocws-etl", key = "Synapse-asagdwpocetl-ConnectionString");

// Create a Properties() object to hold the parameters.

val connectionProperties = new Properties()
val driverClass = "com.microsoft.sqlserver.jdbc.SQLServerDriver"
connectionProperties.setProperty("Driver", driverClass)
val con = DriverManager.getConnection(_url, connectionProperties)
val stmt = con.createStatement()

val create_df = spark.read.format("delta").load("/mnt/trendmicrobif/create_df").select("fullTablename","create") 

for (row <- create_df.collect()){
    
    val fullTableName = row(0) //fullTableName

    val create = row(1)//.create
//     val drop = f"drop talbe $fullTableName%s"

//     println(create)
    val query = f"""select OBJECT_ID('$fullTableName%s') as ObjectId """
  
   
    val df_table_exist = (spark.read
                    .format("com.databricks.spark.sqldw")
                    .option("url", _url)
                    .option("tempDir", "abfss://bifconnect@gdwpocdls.dfs.core.windows.net/tempDirs")
                    .option("useAzureMSI", "true")
                    .option("query", query)
                    .load()
                   );
        
    val df_table_exist_rdd = df_table_exist.collect()
    
    if (df_table_exist_rdd(0)(0) == null){ 
       //is_table_exist = true 
       println(f"$fullTableName%s")
//        stmt.execute(drop)
       stmt.execute(create.asInstanceOf[String])
       println("table created")
    }
}
    

In [0]:
%scala
//  import java.sql.DriverManager
//  import java.sql.Connection
//  import java.util.Properties
 
//  // Create the JDBC URL without passing in the user and password parameters.
//  val jdbcUrl = dbutils.secrets.get(scope = "BIFC-asagdwpocws-etl", key = "Synapse-asagdwpocetl-ConnectionString");

//  // Create a Properties() object to hold the parameters.
//  val connectionProperties = new Properties()

// val driverClass = "com.microsoft.sqlserver.jdbc.SQLServerDriver"
//  connectionProperties.setProperty("Driver", driverClass)
     
//  val con = DriverManager.getConnection(jdbcUrl, connectionProperties)
//  val stmt = con.createStatement()
     
//  stmt.execute("create table BIF_CONNECT.OSCE_Endpoint_Setting5 ([File_ID] [bigint],[File_Date] [date], [group] [varchar](100) NOT NULL,[column_name] [varchar](1000) NULL, [column_value] [nvarchar](1000) NULL)WITH(DISTRIBUTION = ROUND_ROBIN,CLUSTERED COLUMNSTORE INDEX)")

**Insert data into the table in synapse**

use function to get the parse result:  
df = parse_data(parse_data(project_name, group_name, project_group_id, result_type, startdate, enddata, with_file_date)

In [0]:
# PRC_SEL_XML_PARSER_RESULT

create_df_1 = create_df.filter("result_type==1") 
create_df_2 = create_df.filter("result_type==2") 

display(create_df_2)

col create data_source_view fullTableName group_name project_group_id result_type with_file_date [File_ID],[File_Date],[Product_PccNT_Build],[GUID],[Product_Version_Build],[Protocol_Version],[Seat] create table TEST.OSCE_Feedback_Main([File_ID] [bigint],[File_Date] [date],[Product_PccNT_Build] [varchar](15),[GUID] [varchar](54),[Product_Version_Build] [varchar](14),[Protocol_Version] [int],[Seat] [int])WITH(DISTRIBUTION = ROUND_ROBIN,CLUSTERED COLUMNSTORE INDEX) null TEST.OSCE_Feedback_Main OSCE_1.0_Feedback_Main 240 2 true [File_ID],[File_Date],[Count],[DB_Size],[Platform_Type] create table TEST.OSCE_iES_Endpoint_Policy_DB_Size([File_ID] [bigint],[File_Date] [date],[Count] [int],[DB_Size] [int],[Platform_Type] [varchar](13))WITH(DISTRIBUTION = ROUND_ROBIN,CLUSTERED COLUMNSTORE INDEX) null TEST.OSCE_iES_Endpoint_Policy_DB_Size OSCE_2.0_iES_Endpoint_Policy_DB_Size 432 2 true [File_ID],[File_Date],[Count],[Source_Type] create table TEST.OSCE_iES_Server_Impact_Eval_Source([File_ID] [bigint],[File_Date] [date],[Count] [int],[Source_Type] [varchar](34))WITH(DISTRIBUTION = ROUND_ROBIN,CLUSTERED COLUMNSTORE INDEX) null TEST.OSCE_iES_Server_Impact_Eval_Source OSCE_2.0_iES_Server_Impact_Eval_Source 440 2 true [File_ID],[File_Date],[Count],[Match_Method_ID] create table TEST.OSCE_iAC_Agent_Rule_Method_Result([File_ID] [bigint],[File_Date] [date],[Count] [int],[Match_Method_ID] [int])WITH(DISTRIBUTION = ROUND_ROBIN,CLUSTERED COLUMNSTORE INDEX) null TEST.OSCE_iAC_Agent_Rule_Method_Result OSCE_2.0_iAC_Agent_Rule_Method_Result 426 2 true [File_ID],[File_Date],[Count],[Upload_Enabled],[Platform_Type] create table TEST.OSCE_iES_Endpoint_Policy_Meta_Upload([File_ID] [bigint],[File_Date] [date],[Count] [int],[Upload_Enabled] [int],[Platform_Type] [varchar](13))WITH(DISTRIBUTION = ROUND_ROBIN,CLUSTERED COLUMNSTORE INDEX) null TEST.OSCE_iES_Endpoint_Policy_Meta_Upload OSCE_2.0_iES_Endpoint_Policy_Meta_Upload 434 2 true [File_ID],[File_Date],[AC] create table TEST.OSCE_iVP_AC([File_ID] [bigint],[File_Date] [date],[AC] [varchar](65))WITH(DISTRIBUTION = ROUND_ROBIN,CLUSTERED COLUMNSTORE INDEX) null TEST.OSCE_iVP_AC OSCE_2.0_iVP_AC 442 2 true [File_ID],[File_Date],[Last_Updated_Time],[Feedback_Version],[Seat],[S_Agent_Grouping],[TMCM_Enabled],[Product_Database_Mode],[GUID],[Product_HTTP_Server_Type],[Product_OS_Language],[Product_OS_Type],[Product_OS_Code],[Product_PccNT_Build],[Product_Language],[Product_Version_Build],[Product_Upgrade],[Protocol_Version],[Product_SQL_Auth_Mode],[E_Meerkat_Log_Only_Disabled_Count],[E_Meerkat_Log_Only_Enabled_Count],[S_BT_SO_Use_CM],[S_Role_Service],[DAC_Policy_Count],[DLP_Policy_Count],[S_Agent_OUS_Count],[S_Allow_Agent_Update_From_OUS],[S_Custom_Scan_Server_List_Count],[S_Endpoint_Location],[S_Hybrid_Mode],[S_Internal_Proxy_Type],[S_Use_Custom_Scan_Server],[iAC_Agent_Enabled_Count],[iAC_Base_Action],[iAC_Policy],[iAC_Product_Language],[iAC_Product_Version],[iAC_Assign_Rule_Enabled],[iAC_Assign_Rule_With_AD_Enabled],[iAC_Config_Rule_Enabled],[iAC_OS_Arch],[iAC_OS_Branch],[iAC_OS_Build],[iAC_OS_Platform],[iAC_OS_Service_Pack],[iAC_OS_Version],[iAC_OS_Version_Number],[iATAS_Agent_Enabled_Count],[iES_Is_MDR_Enabled],[iES_Maximum_Metadata_Storage],[iES_Product_Build],[iES_Product_Version],[iVP_Agent_Enabled_Count],[TMCM_Proxy_Sock],[S_NAT_Enabled],[Product_Patch],[Product_Service_Pack_Patch],[Product_Service_Pack],[S_Sample_Submission_Count_In_BIF_Period],[Product_SQL_Server_Verion],[S_Update_Source_Type],[S_Use_CM_Proxy],[iAC_Config_Policy_Enabled],[iVP_Endpoint_IPS_Enabled_Client_Count],[iVP_Manual_Enable_IPS_Rule],[iES_Maximum_Redis_Storage],[iES_SaaS_Storage_License],[XDR_Onboard_Accept_XBC],[XDR_Onboard_Get_Onboard_URL],[XDR_Onboard_Is_Onboarded],[XDR_Onboard_Prepare_XBC_Patch],[BIF_Status],[CLP_ID],[BIF_Feedback_Days],[XDR_Onboard_Enable_Onboard_Promotion],[XDR_Onboard_Enable_Pre_Onboard],[XDR_Onboard_Enable_Scheduled_Preonboard],[XDR_Onboard_XBC_Download_Mac_Universal],[XDR_Onboard_XBC_Download_URL_Win32],[XDR_On

**insert synapse a temp table**

In [0]:
for row in create_df_2.collect():
   
    fullTableName = row.fullTableName
    data_source_view = row.data_source_view
    project_group_id = row.project_group_id
    #col =row.col
    result_type = row.result_type
    with_file_date = row.with_file_date
    
  
    if data_source_view == None:
        # parse _data det dataframe from xml source data
        try:
            parse_df = parse_data(None,None,project_group_id,result_type,START_DATE,END_DATE,with_file_date)
            display(parse_df)
            
            if (parse_df.count()>0):
                print(project_group_id, f"{fullTableName}_1")
                (parse_df.write
                    .format("com.databricks.spark.sqldw")
                    .option("useAzureMSI", "true")
                    .option("dbTable", f'{fullTableName}_1')
                    .option("url", _url)
                    .option("tempdir", "abfss://bifconnect@gdwpocdls.dfs.core.windows.net/tempDirs")
                    .save()
                )
        except Exception as e:
            print(e)
    else:
        print(f'{fullTableName} {data_source_view}')

name 'parse_data' is not defined
name 'parse_data' is not defined
name 'parse_data' is not defined
name 'parse_data' is not defined
name 'parse_data' is not defined
name 'parse_data' is not defined
name 'parse_data' is not defined
name 'parse_data' is not defined
name 'parse_data' is not defined
name 'parse_data' is not defined
name 'parse_data' is not defined
name 'parse_data' is not defined
name 'parse_data' is not defined
name 'parse_data' is not defined
name 'parse_data' is not defined
name 'parse_data' is not defined
name 'parse_data' is not defined
name 'parse_data' is not defined
name 'parse_data' is not defined
name 'parse_data' is not defined
name 'parse_data' is not defined
name 'parse_data' is not defined
name 'parse_data' is not defined
name 'parse_data' is not defined
name 'parse_data' is not defined
name 'parse_data' is not defined
name 'parse_data' is not defined
name 'parse_data' is not defined
name 'parse_data' is not defined
name 'parse_data' is not defined
name 'parse_data' is not defined
name 'parse_data' is not defined
name 'parse_data' is not defined

**insert into fullTableName from temptable**

In [0]:
%scala
import java.sql.DriverManager
import java.sql.Connection
import java.util.Properties

//  Create the JDBC URL without passing in the user and password parameters.
spark.conf.set("fs.azure.account.key.gdwpocdls.dfs.core.windows.net", dbutils.secrets.get(scope = "BIFC-asagdwpocws-etl", key = "StorageAccount-gdwpocdls-AccessKey"));
val _url = dbutils.secrets.get(scope = "BIFC-asagdwpocws-etl", key = "Synapse-asagdwpocetl-ConnectionString");

// Create a Properties() object to hold the parameters.
val connectionProperties = new Properties()
val driverClass = "com.microsoft.sqlserver.jdbc.SQLServerDriver"
connectionProperties.setProperty("Driver", driverClass)
val con = DriverManager.getConnection(_url, connectionProperties)
val stmt = con.createStatement()

val create_df = spark.read.format("delta").load("/mnt/trendmicrobif/create_df").select("fullTablename","col","result_type") 
val create_df_1 = create_df.filter("result_type==2")

for (row <- create_df_1.collect()){
    
    val fullTableName = row(0) //fullTableName
    val fullTableName_1 = row(0)+"_1" //fullTableName1
    var insert = ""
    val drop = f"IF OBJECT_ID(N'$fullTableName_1%s') IS NOT NULL BEGIN drop table $fullTableName_1%s END"
    val col = row(1)
    val result_type = row(2)
    try{
      if (result_type == 2 ){
        insert = f"IF OBJECT_ID(N'$fullTableName_1%s') IS NOT NULL BEGIN insert into $fullTableName%s select $col%s from $fullTableName_1%s END"
      }else{
        insert = f"IF OBJECT_ID(N'$fullTableName_1%s') IS NOT NULL BEGIN  insert into $fullTableName%s select * from $fullTableName_1%s END"
      }
      stmt.execute(insert)
      stmt.execute(drop)
      
    }catch{
           case e: Throwable => {
             println(fullTableName)
             println(e.getClass().getName())
           }
       }   
}

In [0]:
(df.write.format("com.databricks.spark.sqldw")
         .option("useAzureMSI", "true")
         .mode("append")
         .option("url", _url)
         .option("dbTable", "TEST.OSCE_Server_Plugin_1")
         .option("tempdir", "abfss://bifconnect@gdwpocdls.dfs.core.windows.net/tempDirs")
         .save()
)


In [0]:
%scala
import java.sql.DriverManager
import java.sql.Connection
import java.util.Properties

//  Create the JDBC URL without passing in the user and password parameters.
spark.conf.set("fs.azure.account.key.gdwpocdls.dfs.core.windows.net", dbutils.secrets.get(scope = "BIFC-asagdwpocws-etl", key = "StorageAccount-gdwpocdls-AccessKey"));
val _url = dbutils.secrets.get(scope = "BIFC-asagdwpocws-etl", key = "Synapse-asagdwpocetl-ConnectionString");

// Create a Properties() object to hold the parameters.

val connectionProperties = new Properties()
val driverClass = "com.microsoft.sqlserver.jdbc.SQLServerDriver"
connectionProperties.setProperty("Driver", driverClass)
val con = DriverManager.getConnection(_url, connectionProperties)
val stmt = con.createStatement()

val insert = "insert into TEST.OSCE_Server_Plugin select [File_ID],[File_Date],[Plugin_Name],[Plugin_Status],[Plugin_Version] from TEST.OSCE_Server_Plugin_1"
val drop = "drop table TEST.OSCE_Server_Plugin_1"

stmt.execute(insert)
stmt.execute(drop)
    

**Parse XML result def**

In [0]:
df = parse_data(None,None,159,1,START_DATE,END_DATE,True)
display(df)

In [0]:
df = parse_data(None,None,159,2,START_DATE,END_DATE,True)
display(df)

In [0]:
from functools import reduce
from pyspark.sql import DataFrame

from pyspark.sql.window import Window
from pyspark.sql.functions import monotonically_increasing_id, row_number
    
def parse_data(project_name, group_name, project_group_id, result_type, startdate, enddata, with_file_date):

    
    if project_group_id == None:
        df_group = ( spark.sql("select * from TBL_PROJECT_GROUP")
                    .filter(F.col('Project_Name') == project_name)
                    .filter(F.col('Group_Name') == group_name)
                    .select('Project_Group_id')
                    )
        project_group_id = df_group.collect()[0][0]

#         df_group = (spark.read
#             .format('com.databricks.spark.sqldw')
#             .option('url', _url)
#             .option('tempDir', 'abfss://bifconnect@gdwpocdls.dfs.core.windows.net/tempDirs')
#             .option('useAzureMSI', 'true')
#             .option('dbTable', 'BIFC_ETL.TBL_PROJECT_GROUP')
#             .load()
       
    #     df_parse_config = (spark.read
    #             .format('com.databricks.spark.sqldw')
    #                     .option('url', _url)
    #                     .option('tempDir', 'abfss://bifconnect@gdwpocdls.dfs.core.windows.net/tempDirs')
    #                     .option('useAzureMSI', 'true')
    #                     .option('dbTable', 'BIFC_ETL.TBL_XML_PARSER_CONFIG')
    #                     .load()
    #                     .withColumn("sort",F.col("sort").cast(IntegerType()))
    #                     .filter(f'project_group_id=={project_group_id}')
    #                    )
    df_parse_config = (spark.sql("select * from TBL_XML_PARSER_CONFIG")
                        .withColumn("sort",F.col("sort").cast(IntegerType()))
                    .filter(f'project_group_id=={project_group_id}')
                      )
#     df_raw_config = (spark.read
#                         .format('com.databricks.spark.sqldw')
#                         .option('url', _url)
#                         .option('tempDir', 'abfss://bifconnect@gdwpocdls.dfs.core.windows.net/tempDirs')
#                         .option('useAzureMSI', 'true')
#                         .option('dbTable', 'BIFC_ETL.TBL_XML_RAW_CONFIG')
#                         .load()
#                        )
    df_parse_config = (spark.sql("select * from TBL_XML_PARSER_CONFIG")
                        .withColumn("sort",F.col("sort").cast(IntegerType()))
                    .filter(f'project_group_id=={project_group_id}')
                      )
    df_raw_config = spark.sql("select * from TBL_XML_RAW_CONFIG")
    
    df_config_table = (df_parse_config.alias('m')
                      .filter(f'project_group_id=={project_group_id}')
                      .join(df_raw_config.alias('r'), [F.col('m.xpath_id')==F.col('r.xpath_id')], 'inner')
                      .drop(df_raw_config.xpath_id)
                      )

    df_config_table_list = df_config_table.select('source','xml_version','category').collect()

    source = df_config_table_list[0][0]
    xml_version =  df_config_table_list[0][1]
    category =  df_config_table_list[0][2]

    # df_config_table_list = df_config_table.filter("master_detail = 'D'").orderBy(F.col("level").desc()).select('raw_group_root','level').collect()
    # root_node = df_config_table_list[0][0]
    # level =  df_config_table_list[0][1]
#     df_raw = (spark.read
#           .format('com.databricks.spark.sqldw')
#           .option('url', _url)
#           .option('tempDir', 'abfss://bifconnect@gdwpocdls.dfs.core.windows.net/tempDirs')
#           .option('useAzureMSI', 'true')
#           .option('dbTable', 'BIFC.TBL_DATA_RAW')
#           .load()
#           .filter(F.col('source') == source)
#           .filter(F.col('xml_version') == xml_version )
#           .filter(F.col('file_date') > startdate)
#           .filter(F.col('file_date') < enddata)
#           .withColumn('file_date', F.date_format(F.col('file_date'),"yyyy/MM/dd"))
#           )

#     df_raw.createOrReplaceTempView('TBL_DATA_RAW')
   
    
    if category != None and result_type == 2:
        df_t_col = (df_config_table
                    .withColumn('category', F.lit(''))
                    .withColumn('column_name', F.when(F.col('category').isNotNull(), F.concat(F.col('category'),F.lit('_'),F.col('column_name'))).otherwise(F.col('column_name')))
                    .groupBy('category','column_name','xpath_id').agg(F.min('sort').alias('sort'))
                    .orderBy(F.col('sort').asc())
                        )
    else:
        df_t_col = (df_config_table
                   .withColumn('category', F.when(F.col('category').isNull(), F.lit('')).otherwise(F.col('category')))
                   .groupBy('category','column_name','xpath_id').agg(F.min('sort').alias('sort'))
                   .orderBy(F.col('sort').asc())
                        )
            
    #debug   
    #display(df_t_col)          
    df_t_col = (df_t_col.alias('r').join(df_config_table.alias('c'),  [F.col('r.xpath_id')==F.col('c.xpath_id')], 'inner')
               .drop('c.xpath_id,c.category,c.column_name,c.sort')
               .orderBy(F.col('r.sort').asc())
               )
    #debug
#     display(df_t_col)

    #generate xpath script , result_type == 1, concat row.  result_type == 2 concat column
    df_t_col_list = df_t_col.collect()

    #init
    with_file_date_col = 'file_date,' if with_file_date==True else ''
    dfs = [] # for type 1
    
    isfristcol = True # for type 2
    w = Window.orderBy(monotonically_increasing_id()) # for type 2

    for r in df_t_col_list:
        xpath = r.xpath 
        xpath_list = xpath.split('/')
        if r.master_detail == 'D':
            if r.xpath == r.raw_group_root:
                xpath_full_text = '/'.join(xpath_list[:-1])+'/'+xpath_list[-1].replace('@','') +'/text()' 
                sql_part_2 = f"xpath(file_content,'{xpath_full_text}')"
            else:
                xpath_full = '/'.join(xpath_list[:-1])+'/@'+xpath_list[-1].replace('@','')  
                sql_part_2 = f"xpath(file_content,'{xpath_full}')"  
        elif (r.master_detail == 'M') :

            xpath_full = '/'.join(xpath_list[:-1])+'/@'+xpath_list[-1].replace('@','') 
            sql_part_2 = f"xpath(file_content,'{xpath_full}')"
        #debug 
        #print(sql_part_2)
        
        if result_type == 1:
            sqlscript = f"""select file_id,{with_file_date_col} {sql_part_2} as column_value from TBL_DATA_RAW"""
            _df = ( spark.sql(sqlscript)
                 .withColumn('category',F.lit(r.category))
                 .withColumn('column_value', F.explode('column_value'))
                 .withColumn('column_name',F.lit(r.column_name))
                
                  )
            dfs.append(_df)     
        elif result_type == 2:
            column_name = r.column_name.replace('.','_')
            if isfristcol == True:
                sqlscript = f"""select file_id,{with_file_date_col}{sql_part_2} as {column_name} from TBL_DATA_RAW"""
                parse_result =( spark.sql(sqlscript)
                     .withColumn(column_name, F.explode(column_name))
                      .withColumn("columnindex", row_number().over(w))
                      )
                isfristcol = False
            else:
                sqlscript = f"""select file_id, {sql_part_2} as {column_name} from TBL_DATA_RAW"""
                _df =( spark.sql(sqlscript)
                     .select(F.explode(column_name).alias(column_name))
                     .withColumn("columnindex", row_number().over(w))
                     )
                parse_result = parse_result.join(_df, parse_result.columnindex == _df.columnindex, 'inner').drop(_df.columnindex)

    #output result df type1 unionall / type2 join all column
    
        
    if with_file_date==True:
        collist = ['file_id','file_date','category','column_name','column_value']
    else:
         collist = ['file_id','category','column_name','column_value']
    
    if result_type == 1:
        parse_result = reduce(DataFrame.unionAll, dfs).select([col for col in collist])
    elif result_type == 2:
        parse_result = parse_result.drop(parse_result.columnindex)

    return parse_result


**Reference Code**

In [0]:
# #type 1 testing
# from functools import reduce
# from pyspark.sql import DataFrame

# category = 'Client_Scan_Mode'
# column_name = '32_bit'
# sqlscript1 = """select file_id, xpath(file_content,'/Data/Products/Product/EndPoint/CPU_Type/@CPU_32bit') as column_value from TBL_DATA_RAW"""
# sqlscript2 = """select file_id, xpath(file_content,'/Data/Products/Product/EndPoint/CPU_Type/@CPU_64bit') as column_value from TBL_DATA_RAW"""

# dfs = []
# parse_result_1 =( spark.sql(sqlscript1)
#              .select('file_id', F.explode('column_value').alias('column_value'))
#              .withColumn('category',F.lit(category))
#              .withColumn('column_name',F.lit(column_name))
#               )
# parse_result_2 =( spark.sql(sqlscript2)
#              .select('file_id', F.explode('column_value').alias('column_value'))
#              .withColumn('category',F.lit(category))
#              .withColumn('column_name',F.lit('64_bit'))
#               )
# dfs.append(parse_result_1)
# dfs.append(parse_result_2)

# df = reduce(DataFrame.unionAll, dfs)
 
# # parse_result = unionAll(parse_result_1,parse_result_2)
# display(df)

In [0]:
# #type2 testing

# from pyspark.sql.window import Window
# from pyspark.sql.functions import monotonically_increasing_id, row_number
# w = Window.orderBy(monotonically_increasing_id())

# sqlscript = """select file_id, xpath(file_content,'/Data/Products/Product/Server/PLS/Item/@Version') as Plugin_Version,
# xpath(file_content,'/Data/Products/Product/Server/PLS/Item/@Name') as Plugin_Name, 
# xpath(file_content,'/Data/Products/Product/Server/PLS/Item/@Status') as Plugin_Status
# from TBL_DATA_RAW"""

# parse_result_1 =( spark.sql(sqlscript)
#              .select('file_id',F.explode('Plugin_Version').alias('Plugin_Version'))
#               .withColumn("columnindex", row_number().over(w))
#               )

# parse_result_2 =( spark.sql(sqlscript)
#                .select( F.explode('Plugin_Name').alias('Plugin_Name'))
#                  .withColumn("columnindex", row_number().over(w))
#               )
# parse_result_3 =( spark.sql(sqlscript)
#              .select(F.explode('Plugin_Status').alias('Plugin_Status'))
#                   .withColumn("columnindex", row_number().over(w))
#               )
 

# parse_result_1 = parse_result_1.join(parse_result_2, parse_result_2.columnindex == parse_result_1.columnindex, 'inner').drop(parse_result_2.columnindex)
# parse_result_1 = parse_result_1.join(parse_result_3, parse_result_3.columnindex == parse_result_1.columnindex, 'inner').drop(parse_result_3.columnindex)
# parse_result_1 = parse_result_1.drop(parse_result_1.columnindex)
# display(parse_result_1)